In [2]:
USERS_RANGE=(1,1000)
SEARCH_PER_USER_RANGE=(10,20)
USERS_EXPORT_FILE="../source_data/users.csv"

In [8]:
# Load current users
import csv
users = []
with open(USERS_EXPORT_FILE, newline='') as csvfile:
    reader = csv.DictReader(csvfile)
    for row in reader:
        users.append(row)
users

[{'Id': '1',
  'Name': 'Daniel Johnson                                                                  ',
  'BirthDate': '1993-01-08',
  'Gender': 'O ',
  'ValidFrom': '2022-05-24',
  'ValidTo': '2999-12-31',
  'LocationId': '12',
  'SegmentId': '5'},
 {'Id': '2',
  'Name': 'Kendra Watkins                                                                  ',
  'BirthDate': '1968-07-25',
  'Gender': 'M ',
  'ValidFrom': '2021-07-19',
  'ValidTo': '2999-12-31',
  'LocationId': '14',
  'SegmentId': '9'},
 {'Id': '3',
  'Name': 'Michael Watson                                                                  ',
  'BirthDate': '1983-02-01',
  'Gender': 'F ',
  'ValidFrom': '2022-01-31',
  'ValidTo': '2999-12-31',
  'LocationId': '15',
  'SegmentId': '6'},
 {'Id': '4',
  'Name': 'Brian Stephenson                                                                ',
  'BirthDate': '1988-11-28',
  'Gender': 'F ',
  'ValidFrom': '2019-03-25',
  'ValidTo': '2999-12-31',
  'LocationId': '2',
  'Segment

In [9]:
# Convert to datetime dates
import datetime
today = datetime.datetime.today()
for user in users:
    user["ValidFrom"] = datetime.datetime.strptime(user["ValidFrom"], "%Y-%m-%d")
    user["ValidTo"] = datetime.datetime.strptime(user["ValidTo"], "%Y-%m-%d") if user["ValidTo"] != '2999-12-31' else today
users

[{'Id': '1',
  'Name': 'Daniel Johnson                                                                  ',
  'BirthDate': '1993-01-08',
  'Gender': 'O ',
  'ValidFrom': datetime.datetime(2022, 5, 24, 0, 0),
  'ValidTo': datetime.datetime(2023, 12, 17, 12, 19, 47, 408258),
  'LocationId': '12',
  'SegmentId': '5'},
 {'Id': '2',
  'Name': 'Kendra Watkins                                                                  ',
  'BirthDate': '1968-07-25',
  'Gender': 'M ',
  'ValidFrom': datetime.datetime(2021, 7, 19, 0, 0),
  'ValidTo': datetime.datetime(2023, 12, 17, 12, 19, 47, 408258),
  'LocationId': '14',
  'SegmentId': '9'},
 {'Id': '3',
  'Name': 'Michael Watson                                                                  ',
  'BirthDate': '1983-02-01',
  'Gender': 'F ',
  'ValidFrom': datetime.datetime(2022, 1, 31, 0, 0),
  'ValidTo': datetime.datetime(2023, 12, 17, 12, 19, 47, 408258),
  'LocationId': '15',
  'SegmentId': '6'},
 {'Id': '4',
  'Name': 'Brian Stephenson            

In [61]:
## For every users, define a number of searchs between the valid dates
import random
from faker import Faker
fake = Faker()

search_id = 0 # Unique id for every search
searchs = []
for user in users:
    for i in range(random.randint(*SEARCH_PER_USER_RANGE)):
        time_id = fake.date_time_between(user["ValidFrom"], user["ValidTo"])+datetime.timedelta(seconds=random.randint(0, 86400))
        searchs.append({
            "Id": search_id, 
            "UserId": user["Id"],
            "TimeId": time_id.strftime("%Y-%m-%d %H:%M:%S"),
            "Query": fake.sentence(),
        })
        search_id +=1
searchs


[{'Id': 0,
  'UserId': '1',
  'TimeId': '2022-08-18 05:38:07',
  'Query': 'Success always world degree general government officer.'},
 {'Id': 1,
  'UserId': '1',
  'TimeId': '2023-03-25 02:58:35',
  'Query': 'Know new pass lose arm debate open.'},
 {'Id': 2,
  'UserId': '1',
  'TimeId': '2022-12-20 11:31:55',
  'Query': 'Together decade recently name.'},
 {'Id': 3,
  'UserId': '1',
  'TimeId': '2023-02-02 07:39:06',
  'Query': 'East study specific size life though paper.'},
 {'Id': 4,
  'UserId': '1',
  'TimeId': '2023-08-16 22:55:30',
  'Query': 'Must coach floor accept.'},
 {'Id': 5,
  'UserId': '1',
  'TimeId': '2023-08-02 05:32:06',
  'Query': 'Public bit work.'},
 {'Id': 6,
  'UserId': '1',
  'TimeId': '2023-01-18 16:18:43',
  'Query': 'Fall debate best could.'},
 {'Id': 7,
  'UserId': '1',
  'TimeId': '2023-06-12 05:56:04',
  'Query': 'Order item factor.'},
 {'Id': 8,
  'UserId': '1',
  'TimeId': '2022-07-23 10:30:04',
  'Query': 'Exactly across police certainly new nothing profe

In [13]:
# Len of the search table
print(len(searchs))

12326


In [50]:
HEADER_USER_SEARCH = """ DELETE FROM public."UserSearch";
INSERT INTO public."UserSearch"( "Id", "UserId", "TimeId", "Query") VALUES
"""
ROW_USER_SEARCH = """ ({Id}, {UserId}, '{TimeId}', '{Query}')"""
USER_SEARCH_FILE = "../19_insert_user_search.sql"

In [63]:
# Create the sql content
sql_user_search = HEADER_USER_SEARCH
sql_user_search += ",\n".join([ROW_USER_SEARCH.format(**search) for search in searchs])
sql_user_search += ";"
sql_user_search

' DELETE FROM public."UserSearch";\nINSERT INTO public."UserSearch"( "Id", "UserId", "TimeId", "Query") VALUES\n (0, 1, \'2022-08-18 05:38:07\', \'Success always world degree general government officer.\'),\n (1, 1, \'2023-03-25 02:58:35\', \'Know new pass lose arm debate open.\'),\n (2, 1, \'2022-12-20 11:31:55\', \'Together decade recently name.\'),\n (3, 1, \'2023-02-02 07:39:06\', \'East study specific size life though paper.\'),\n (4, 1, \'2023-08-16 22:55:30\', \'Must coach floor accept.\'),\n (5, 1, \'2023-08-02 05:32:06\', \'Public bit work.\'),\n (6, 1, \'2023-01-18 16:18:43\', \'Fall debate best could.\'),\n (7, 1, \'2023-06-12 05:56:04\', \'Order item factor.\'),\n (8, 1, \'2022-07-23 10:30:04\', \'Exactly across police certainly new nothing professor.\'),\n (9, 1, \'2023-09-30 07:20:14\', \'Fill interview Mr investment.\'),\n (10, 1, \'2022-12-10 03:34:01\', \'In leg three establish message poor.\'),\n (11, 1, \'2023-10-04 13:44:01\', \'Accept really rather purpose.\'),\n (

In [64]:
with open(USER_SEARCH_FILE, "w") as f:
    f.write(sql_user_search)

In [65]:
# Given current searches lets create the search results
SEARCH_RESPONSE_RANGE=(5,10)
CONTENT_RANGE=(1,4743)
SEARCH_RESPONSE_FILE = "../20_insert_search_response.sql"
SEARCH_RESPONSE_HEADER = """DELETE FROM public."SearchResponse";
INSERT INTO public."SearchResponse"( "SearchId", "ContentId", "Ranking") VALUES
"""
SEARCH_RESPONSE_ROW = "( {SearchId}, {ContentId}, {Ranking})"

In [66]:
from collections import defaultdict
search_response = []
search_response_dict = defaultdict(list)
for search in searchs:
    content=set()
    for i in range(random.randint(*SEARCH_RESPONSE_RANGE)):
        while (new_content := random.randint(*CONTENT_RANGE)) in content: ...
        search_response.append({
            "SearchId": search["Id"],
            "ContentId": new_content,
            "Ranking": i+1,
        })
        content.add(new_content)
    search_response_dict[search["Id"]].extend(content)
search_response

[{'SearchId': 0, 'ContentId': 4685, 'Ranking': 1},
 {'SearchId': 0, 'ContentId': 2000, 'Ranking': 2},
 {'SearchId': 0, 'ContentId': 242, 'Ranking': 3},
 {'SearchId': 0, 'ContentId': 773, 'Ranking': 4},
 {'SearchId': 0, 'ContentId': 2116, 'Ranking': 5},
 {'SearchId': 0, 'ContentId': 2694, 'Ranking': 6},
 {'SearchId': 1, 'ContentId': 314, 'Ranking': 1},
 {'SearchId': 1, 'ContentId': 4415, 'Ranking': 2},
 {'SearchId': 1, 'ContentId': 2654, 'Ranking': 3},
 {'SearchId': 1, 'ContentId': 960, 'Ranking': 4},
 {'SearchId': 1, 'ContentId': 4227, 'Ranking': 5},
 {'SearchId': 1, 'ContentId': 914, 'Ranking': 6},
 {'SearchId': 2, 'ContentId': 276, 'Ranking': 1},
 {'SearchId': 2, 'ContentId': 3406, 'Ranking': 2},
 {'SearchId': 2, 'ContentId': 2991, 'Ranking': 3},
 {'SearchId': 2, 'ContentId': 2382, 'Ranking': 4},
 {'SearchId': 2, 'ContentId': 1628, 'Ranking': 5},
 {'SearchId': 2, 'ContentId': 2341, 'Ranking': 6},
 {'SearchId': 3, 'ContentId': 266, 'Ranking': 1},
 {'SearchId': 3, 'ContentId': 2892, 'R

In [67]:
search_response_sql = SEARCH_RESPONSE_HEADER
search_response_sql += ",\n".join([SEARCH_RESPONSE_ROW.format(**search) for search in search_response])
search_response_sql += ";"
search_response_sql

'DELETE FROM public."SearchResponse";\nINSERT INTO public."SearchResponse"( "SearchId", "ContentId", "Ranking") VALUES\n( 0, 4685, 1),\n( 0, 2000, 2),\n( 0, 242, 3),\n( 0, 773, 4),\n( 0, 2116, 5),\n( 0, 2694, 6),\n( 1, 314, 1),\n( 1, 4415, 2),\n( 1, 2654, 3),\n( 1, 960, 4),\n( 1, 4227, 5),\n( 1, 914, 6),\n( 2, 276, 1),\n( 2, 3406, 2),\n( 2, 2991, 3),\n( 2, 2382, 4),\n( 2, 1628, 5),\n( 2, 2341, 6),\n( 3, 266, 1),\n( 3, 2892, 2),\n( 3, 500, 3),\n( 3, 3359, 4),\n( 3, 2497, 5),\n( 3, 644, 6),\n( 3, 3255, 7),\n( 3, 331, 8),\n( 3, 4698, 9),\n( 3, 1926, 10),\n( 4, 317, 1),\n( 4, 4521, 2),\n( 4, 3671, 3),\n( 4, 69, 4),\n( 4, 1465, 5),\n( 5, 4081, 1),\n( 5, 858, 2),\n( 5, 4387, 3),\n( 5, 3362, 4),\n( 5, 2631, 5),\n( 5, 3977, 6),\n( 5, 1815, 7),\n( 6, 532, 1),\n( 6, 3003, 2),\n( 6, 1110, 3),\n( 6, 915, 4),\n( 6, 4534, 5),\n( 6, 2168, 6),\n( 6, 987, 7),\n( 6, 1210, 8),\n( 6, 2334, 9),\n( 7, 2753, 1),\n( 7, 186, 2),\n( 7, 1923, 3),\n( 7, 1629, 4),\n( 7, 1099, 5),\n( 7, 3236, 6),\n( 7, 65, 7),\n( 7

In [68]:
with open(SEARCH_RESPONSE_FILE, "w") as f:
    f.write(search_response_sql)

In [83]:
## Last add ContentHits based on searche
CONTENT_HITS_FILE = "../21_insert_content_hits_searchs.sql"
CONTENT_HITS_HEADER = """DELETE FROM public."ContentHit" WHERE "SearchId" IS NOT NULL;
INSERT INTO public."ContentHit"( "ContentId", "TimeId", "SearchId", "UserId") VALUES
"""
CONTENT_HITS_ROW = "( {ContentId}, '{TimeId}', {SearchId}, {UserId})"
CONTENT_HITS_RANGE=(0,2)


In [84]:
content_hits_from_search = []
for search in searchs:
    hited_content = set()
    for hits in range(random.randint(*CONTENT_HITS_RANGE)):
        while (hit_content := random.choice(search_response_dict[search["Id"]])) in hited_content: ...
        content_hits_from_search.append( dict(
            ContentId = hit_content,
            UserId = search["UserId"],
            TimeId = search["TimeId"],
            SearchId = search["Id"]            
        ))
        hited_content.add(hit_content)
content_hits_from_search


[{'ContentId': 2000,
  'UserId': '1',
  'TimeId': '2022-08-18 05:38:07',
  'SearchId': 0},
 {'ContentId': 4415,
  'UserId': '1',
  'TimeId': '2023-03-25 02:58:35',
  'SearchId': 1},
 {'ContentId': 2654,
  'UserId': '1',
  'TimeId': '2023-03-25 02:58:35',
  'SearchId': 1},
 {'ContentId': 4698,
  'UserId': '1',
  'TimeId': '2023-02-02 07:39:06',
  'SearchId': 3},
 {'ContentId': 3977,
  'UserId': '1',
  'TimeId': '2023-08-02 05:32:06',
  'SearchId': 5},
 {'ContentId': 2168,
  'UserId': '1',
  'TimeId': '2023-01-18 16:18:43',
  'SearchId': 6},
 {'ContentId': 1099,
  'UserId': '1',
  'TimeId': '2023-06-12 05:56:04',
  'SearchId': 7},
 {'ContentId': 1573,
  'UserId': '1',
  'TimeId': '2023-06-12 05:56:04',
  'SearchId': 7},
 {'ContentId': 1292,
  'UserId': '1',
  'TimeId': '2022-12-10 03:34:01',
  'SearchId': 10},
 {'ContentId': 1168,
  'UserId': '1',
  'TimeId': '2023-10-04 13:44:01',
  'SearchId': 11},
 {'ContentId': 1776,
  'UserId': '1',
  'TimeId': '2022-10-07 10:36:57',
  'SearchId': 1

In [85]:
content_hits_from_search_sql = CONTENT_HITS_HEADER
content_hits_from_search_sql += ",\n".join([CONTENT_HITS_ROW.format(**search) for search in content_hits_from_search])
content_hits_from_search_sql += ";"
content_hits_from_search_sql

'DELETE FROM public."ContentHit" WHERE "SearchId" IS NOT NULL;\nINSERT INTO public."ContentHit"( "ContentId", "TimeId", "SearchId", "UserId") VALUES\n( 2000, \'2022-08-18 05:38:07\', 0, 1),\n( 4415, \'2023-03-25 02:58:35\', 1, 1),\n( 2654, \'2023-03-25 02:58:35\', 1, 1),\n( 4698, \'2023-02-02 07:39:06\', 3, 1),\n( 3977, \'2023-08-02 05:32:06\', 5, 1),\n( 2168, \'2023-01-18 16:18:43\', 6, 1),\n( 1099, \'2023-06-12 05:56:04\', 7, 1),\n( 1573, \'2023-06-12 05:56:04\', 7, 1),\n( 1292, \'2022-12-10 03:34:01\', 10, 1),\n( 1168, \'2023-10-04 13:44:01\', 11, 1),\n( 1776, \'2022-10-07 10:36:57\', 12, 1),\n( 2727, \'2022-10-07 10:36:57\', 12, 1),\n( 3612, \'2023-03-06 13:42:49\', 13, 1),\n( 2534, \'2023-03-06 13:42:49\', 13, 1),\n( 3702, \'2022-09-28 12:20:22\', 14, 2),\n( 4071, \'2022-05-04 01:03:57\', 15, 2),\n( 2344, \'2022-05-04 01:03:57\', 15, 2),\n( 3158, \'2021-11-05 16:50:37\', 16, 2),\n( 2288, \'2021-10-24 20:02:46\', 17, 2),\n( 3389, \'2021-10-24 20:02:46\', 17, 2),\n( 137, \'2022-01-2

In [86]:
with open(CONTENT_HITS_FILE, "w") as f:
    f.write(content_hits_from_search_sql)